In [ ]:
import numpy as np

# Test on KITTI 05

In [ ]:
exec /src/build/kitti_loop_detection /src/data/surf64_k10L6.voc.gz /kitti/05/image_2/ /src/results/confusion_5.txt 5

In [ ]:
T = 5 #interval between frames
confusion = np.loadtxt("../results/confusion_"+str(T)+".txt", delimiter=",", dtype=float)
M = int(200 / T -1) # minimun frames between both ends of an edge
N = confusion.shape[0] # frame number
for i in range(N):
    confusion[i, max(i-M, 0):i+M] = 0

In [ ]:
def read_kitti_pose(pose_path):
    with open(pose_path, 'r') as f:
        lines = f.readlines()
    poses = []
    for line in lines:
        pose = np.eye(4)
        pose_3x4 = np.array(line.strip('\n').split(' ')).reshape(3,4).astype(float)
        pose[:3,:] = pose_3x4
        poses.append(pose)
    return np.array(poses)

odom_poses = read_kitti_pose('/home/link/Projects/curly_slam/data/kitty05/cvo_intensity_img_gpu0_oct25_best/05.txt')
odom_pos = odom_poses[:,:-1,3]
confidence = np.where(confusion>0.05, confusion, 0).max(1)
edges = [(i0, i1) for i0, i1 in enumerate(np.where(confusion>0.05, confusion, 0).argmax(1)) if i1!=0]
edges = [(i0*T, i1*T, confidence[i0]) for i0, i1 in edges]
edges = [x for x in edges if np.linalg.norm(odom_poses[x[0],:-1,3]-odom_poses[x[1],:-1,3])<60]

In [ ]:
[(*x, np.linalg.norm(odom_pos[x[0]]-odom_pos[x[1]])) for x in edges]

In [ ]:
# plot ground truth and edges with plotly
import plotly.graph_objects as go
fig = go.Figure()
fig.add_trace(go.Scatter3d(
    x=odom_poses[:,0,3],
    y=odom_poses[:,1,3],
    z=odom_poses[:,2,3],
    mode='markers',
    marker=dict(
        size=0.5,
        color='blue',
        opacity=0.3
    )
))
for edge in edges:
    i0, i1, confidence = edge
    # print(i0, i1, odom_poses[i0,:-1,3]-odom_poses[i1,:-1,3])
    fig.add_trace(go.Scatter3d(
        x=[odom_poses[i0,0,3], odom_poses[i1,0,3]],
        y=[odom_poses[i0,1,3], odom_poses[i1,1,3]],
        z=[odom_poses[i0,2,3], odom_poses[i1,2,3]],
        mode='lines',
        line=dict(
            color='red',
            width=2
        ),
        text=f'{i0}->{i1} {confidence}'
    ))
fig.show()


In [ ]:
from spatialmath import *
from spatialmath.base import trnorm, r2q, qprint

gt_poses = read_kitti_pose('/home/link/Projects/curly_slam/data/kitty05/groundtruth.txt')
gt_poses = SE3([trnorm(pose) for pose in gt_poses])
lines = []
for i0, i1, confidence in edges:
    relative_pose = gt_poses[i0].inv() * gt_poses[i1]
    t, q = relative_pose.t, r2q(relative_pose.R)
    vertex_line = f'VERTEX_SE3:QUAT {i} {t[0]} {t[1]} {t[2]} {q[0]} {q[1]} {q[2]} {q[3]}'
    line = f'EDGE_SE3:QUAT {i0} {i1} {t[0]} {t[1]} {t[2]} {q[1]} {q[2]} {q[3]} {q[0]} '
    line += ' '.join([str(confidence) if x in [0,6,11,15,18,20] else '0' for x in range(21)])
    lines.append(line)
edges_poses_file = '/home/link/Projects/curly_slam/data/kitty05/edges.g2o.txt'
with open(edges_poses_file, 'w') as f:
    f.writelines('\n'.join(lines))

In [ ]:
SE3()*np.ones((3,1))

In [ ]:
# plot matches
# import cv2
# dataset_folder = '/home/link/Projects/unified_cvo/test_data/kitti_05/image_2/'
# for i0, i1 in zip(index0, index1):
#     output_file.write(str(i0)+' '+str(i1)+'\n')
#     img1 = cv2.imread(dataset_folder+'0'*(6-len(str(i0)))+str(i0)+'.png')
#     img2 = cv2.imread(dataset_folder+'0'*(6-len(str(i1)))+str(i1)+'.png')
#     vis = np.concatenate((img1, img2), axis=0)
#     cv2.imwrite('../results/matches/'+str(i1)+'.png', vis)


In [ ]:
qprint(r2q(relative_pose.R)),r2q(relative_pose.R)

# TEST 00 02 05 06 07 08

In [ ]:
command = 'echo -e "'
for i in [0, 2, 5, 6, 7, 8]:
    command += f'exec /src/build/kitti_loop_detection /src/data/surf64_k10L6.voc.gz /kitti/0{i}/image_2/ /src/results/confusion_seq0{i}_5.txt 5\\n'
command += '" | parallel'
print(command)

In [3]:
import numpy as np
from spatialmath import *
import plotly.graph_objects as go
from plotly.subplots import make_subplots

def read_kitti_pose(pose_path):
    with open(pose_path, 'r') as f:
        lines = f.readlines()
    poses = []
    for line in lines:
        pose = np.eye(4)
        pose_3x4 = np.array(line.strip('\n').split(' ')).reshape(3,4).astype(float)
        pose[:3,:] = pose_3x4
        poses.append(pose)
    return np.array(poses)

# create figure
_ = {'type': 'surface'}
fig = make_subplots(rows=3, cols=2, subplot_titles=("Seq 00", "Seq 02", "Seq 05", "Seq 06", "Seq 07", "Seq 08"),
    specs=[[_, _], [_, _], [_, _]])
fig.update_layout(width=1200, height=1200)

# process each sequence
for subplot_index, seq_index in enumerate([0, 2, 5, 6, 7, 8]):
    print('processing sequence', seq_index)
    # params
    T = 5 #interval between frames
    confusion_path = f"../results/confusion_seq0{seq_index}_{T}.txt"
    odom_path = f"../results/cvo/0{seq_index}.txt"
    gt_path = f'/media/sdg1/rzh/kitti/kitti/sequences/0{seq_index}/groundtruth.txt'
    M = int(200 / T -1) # minimun frames between both ends of an edge
    # load confusion
    confusion = np.loadtxt(confusion_path, delimiter=",", dtype=float)
    N = confusion.shape[0] # frame number
    # fill diagonal with zeros
    for i in range(N):
        confusion[i, max(i-M, 0):i+M] = 0
    # load odom
    odom_poses = read_kitti_pose(odom_path)
    odom_pos = odom_poses[:,:-1,3]
    # load ground truth
    gt_poses = read_kitti_pose(gt_path)
    # get edges
    confidence = np.where(confusion>0.05, confusion, 0).max(1)
    inliers = np.where(confusion>0.05, confusion, 0)
    edges = [(i0, i1) for i0, i1 in enumerate(inliers.argmax(1)) if i1!=0]
    edges = [(i0*T, i1*T, confidence[i0]) for i0, i1 in edges]
    edges = [x for x in edges if np.linalg.norm(odom_poses[x[0],:-1,3]-odom_poses[x[1],:-1,3])<70 or x[2]>0.07]
    # plot odom
    fig.add_trace(go.Scatter3d(
        x=odom_poses[:,0,3],
        y=odom_poses[:,1,3],
        z=odom_poses[:,2,3],
        mode='markers',
        marker=dict(
            size=0.5,
            color='blue',
            opacity=0.3
        )
    ), row=subplot_index//2+1, col=subplot_index%2+1)
    # plot ground truth
    fig.add_trace(go.Scatter3d(
        x=gt_poses[:,0,3]+500,
        y=gt_poses[:,1,3],
        z=gt_poses[:,2,3],
        mode='markers',
        marker=dict(
            size=0.5,
            color='green',
            opacity=0.3
        )
    ), row=subplot_index//2+1, col=subplot_index%2+1)
    # plot edges
    for edge in edges:
        i0, i1, confidence = edge
        # print(i0, i1, odom_poses[i0,:-1,3]-odom_poses[i1,:-1,3])
        fig.add_trace(go.Scatter3d(
            x=[odom_poses[i0,0,3], odom_poses[i1,0,3]],
            y=[odom_poses[i0,1,3], odom_poses[i1,1,3]],
            z=[odom_poses[i0,2,3], odom_poses[i1,2,3]],
            mode='lines',
            line=dict(
                color='red',
                width=2
            ),
            text=f'{i0}->{i1} {confidence}',
            legendgroup='edges'
        ), row=subplot_index//2+1, col=subplot_index%2+1)

# show figure
fig.show()


processing sequence 0
processing sequence 2
processing sequence 5
processing sequence 6
processing sequence 7
processing sequence 8
